In [1]:
import pandas as pd

# display all pandas columns
pd.set_option('display.max_columns', None)  # Show all columns

## Data import

In [2]:
df_traffic_data = pd.read_excel('../../data/raw/traffic_sensors_locations/all_sensors.xlsx') 
df_air_quality_and_locations = pd.read_parquet("../../data/processed/air/df_air_quality_and_locations_from_2013.parquet")

In [3]:
len(df_traffic_data)

5095

In [4]:
len(df_traffic_data.drop_duplicates(subset=['longitud', 'latitud']))

4941

In [5]:
len(df_air_quality_and_locations)

2490936

In [6]:
len(df_air_quality_and_locations.drop_duplicates(subset=["LONGITUD", "LATITUD"]))

24

In [7]:
# Remove duplicates for air quality data
df_air_quality_and_locations = df_air_quality_and_locations.drop_duplicates(subset=["LONGITUD", "LATITUD"])

# Remove duplicates for traffic data
df_traffic_data = df_traffic_data.drop_duplicates(subset=['longitud', 'latitud'])  # Assuming 'id' is the identifier for the traffic sensor

In [8]:
df_traffic_data = df_traffic_data.rename(columns = {'id':'id_trafico'}) 

In [10]:
df_air_quality_and_locations.columns = df_air_quality_and_locations.columns.str.lower()
df_air_quality_and_locations = df_air_quality_and_locations.rename(columns = {'codigo':'id_no2'})

In [15]:
len(df_air_quality_and_locations)

24

## Visualization

In [43]:
import folium


# Create a map centered around the average coordinates of the NO2 sensors
map_center = [df_air_quality_and_locations["LATITUD"].mean(), df_air_quality_and_locations["LONGITUD"].mean()]
m = folium.Map(location=map_center, zoom_start=12)

# Add CircleMarkers for NO2 sensors
for _, row in df_air_quality_and_locations.iterrows():
    folium.CircleMarker(
        location=[row["LATITUD"], row["LONGITUD"]],
        radius=8,  # Size of the circle
        color='blue',  # Color for NO2 sensors
        fill=True,
        fill_color='blue',
        fill_opacity=0.9,
        popup=f'Sensor NO2: {row["LONGITUD"]}, {row["LATITUD"]}'
    ).add_to(m)

# Add CircleMarkers for traffic sensors
for _, row in df_traffic_data.iterrows():
    folium.CircleMarker(
        location=[row["latitud"], row["longitud"]],
        radius=2,  # Size of the circle
        color='red',  # Color for traffic sensors
        fill=True,
        fill_color='red',
        fill_opacity=0.1,
        popup=f'Sensor Traffic: {row["id"]}, {row["latitud"]}, {row["longitud"]}'
    ).add_to(m)

# Display the map
m

## Mapear Sensores de NO2 con sensores de Trafico

`Para ello, como primera iteracion, nos quedaremos solo con los sensores de NO2 que tengan al menos un sensor de trafico en el radio de 200 metros. En el caso de que no haya sensores, no usaremos ese sensor de NO2. En el caso de que haya mas de uno, usaremos los valores intercuartiles.`

In [44]:
#porque antes he eliminado duplicados...
df_traffic_data = pd.read_excel('../../data/raw/traffic_sensors_locations/all_sensors.xlsx') 

In [45]:
df_air_quality_and_locations = df_air_quality_and_locations[['CODIGO','LATITUD','LONGITUD']]
df_traffic_data = df_traffic_data[['id','latitud','longitud']]

df_air_quality_and_locations = df_air_quality_and_locations.rename(columns={'CODIGO':'id_no2'})
df_traffic_data = df_traffic_data.rename(columns={'id':'id_trafico'})

df_air_quality_and_locations['id_no2'] = df_air_quality_and_locations['id_no2'].astype(str)
df_traffic_data['id_trafico'] = df_traffic_data['id_trafico'].astype(str)


In [50]:
import pandas as pd
import numpy as np
from scipy.spatial import cKDTree

# ------------------------
# 2. Convertir coordenadas a radianes
# ------------------------
df_air_quality_and_locations[['latitud_rad', 'longitud_rad']] = np.radians(df_air_quality_and_locations[['LATITUD', 'LONGITUD']])
df_traffic_data[['latitud_rad', 'longitud_rad']] = np.radians(df_traffic_data[['latitud', 'longitud']])

# ------------------------
# 3. Construcción del KDTree para búsqueda eficiente
# ------------------------
tree = cKDTree(df_traffic_data[['latitud_rad', 'longitud_rad']])

# Definir radio en radianes (200m ≈ 0.0018 rad)
radio = 200 / 6371000  # Radio de la Tierra en metros

# ------------------------
# 4. Asignación de sensores de tráfico a cada sensor de NO2
# ------------------------
asignaciones = []

for i, row in df_air_quality_and_locations.iterrows():
    idx_cercanos = tree.query_ball_point([row['latitud_rad'], row['longitud_rad']], radio)
    
    for idx in idx_cercanos:
        distance = round(tree.query([row['latitud_rad'], row['longitud_rad']], k=1)[0] * 6371000)  # Convert from radians to meters
        
        asignaciones.append({
            'id_no2': row['id_no2'],
            'id_trafico': df_traffic_data.iloc[idx]['id_trafico'],
            'distance_m': distance  # New column for distance
        })

df_mapping_no2_to_traffic = pd.DataFrame(asignaciones)

In [51]:
df_mapping_no2_to_traffic

id_no2 id_trafico  distance_m
0   28079004      10647          71
1   28079004       4333          71
2   28079004       4313          71
3   28079004       4285          71
4   28079004       3732          71
..       ...        ...         ...
66  28079056       6822          24
67  28079056      10332          24
68  28079056      10848          24
69  28079056      10849          24
70  28079056      11006          24

[71 rows x 3 columns]

In [52]:
df_mapping_no2_to_traffic.to_csv("../../data/processed/mapping/no2_to_traffic_sensor_mapping.csv" ,index=False)

In [49]:
df_mapping_no2_to_traffic.id_trafico.nunique()

71